# **Assistente de IA para Companhia Aérea**

 ## Este projeto visa desenvolver um assistente de suporte ao cliente utilizando IA para uma companhia aérea chamada aérea FlyAir. O objetivo é criar um chatbot interativo capaz de responder perguntas sobre passagens, destinos e serviços oferecidos pela empresa.

## Tecnologias Utilizadas
- **OpenAI GPT-4o-mini** para processamento de linguagem natural
- **Gradio** para interface interativa
- **DALL·E-3** para geração de imagens
- **Python** para desenvolvimento

## Funcionalidades do Assistente
### 1. Chatbot de Atendimento
- Responde a perguntas sobre passagens, check-in, bagagens e políticas da companhia.
- Mantém respostas curtas, precisas e educadas.

### 2. Consulta de Preços de Passagens
- O assistente pode consultar e retornar o preço das passagens para destinos específicos.
- Utiliza uma função integrada para acessar informações de preços armazenadas.

### 3. Geração de Imagens de Destinos
- Gera imagens representativas dos destinos a partir de prompts personalizados.

### 4. Geração de Áudio (Opcional)
- O assistente pode transformar respostas em áudio utilizando modelos de voz da OpenAI.

## Estrutura do Agente
- **Divisão de tarefas:** separa problemas complexos em etapas menores.
- **Uso de ferramentas:** o modelo pode chamar funções para realizar tarefas específicas.
- **Ambiente interativo:** permite interação com usuários através de um chatbot integrado.

## Implementação
### 1. Configuração do Ambiente
- Importação de bibliotecas (OpenAI, Gradio, dotenv, JSON, entre outras).
- Carregamento da chave da API OpenAI.

### 2. Desenvolvimento do Chatbot
- Implementação de uma interface de chat utilizando **Gradio**.
- Configuração do modelo **GPT-4o-mini** para responder aos usuários.
- Manutenção do histórico de conversa para um atendimento mais natural.

### 3. Integração com Funções Específicas
- Criação de uma função para consultar preços de passagens.
- Implementação da função de geração de imagens para representar destinos.
- Opção de geração de áudio para interação multimodal.

## Execução do Projeto
- O assistente será executado localmente utilizando **Gradio**, permitindo testes e interação com os usuários.
- Possibilidade de expor o assistente online utilizando **Gradio Share** para testes em ambiente real.

## Conclusão
Este projeto visa criar um assistente de IA funcional para uma companhia aérea, oferecendo suporte ao cliente de forma eficiente e automatizada. Com o uso de modelos de linguagem avançados, o sistema poderá responder dúvidas, fornecer informações de passagens e gerar conteúdo multimodal para melhorar a experiência do usuário.

## Importações das Bibliotecas

In [59]:
import os
import json
from dotenv import load_dotenv
from openai import OpenAI
import gradio as gr
# Algumas importações para manipulação de imagens
import base64
from io import BytesIO
from PIL import Image

## Inicializando a API OpenAI e Definindo o Modelo

In [60]:
load_dotenv()
chave_api_openai = os.getenv('OPENAI_API_KEY')
if chave_api_openai:
    print(f"A chave da API OpenAI existe e começa com {chave_api_openai[:8]}")
else:
    print("Chave da API OpenAI não definida")

MODELO = "gpt-4o-mini"
openai = OpenAI() 


A chave da API OpenAI existe e começa com sk-proj-


## Definindo o Sistema de Prompts

In [61]:
# Mensagem do sistema que orienta o comportamento do assistente
mensagem_sistema = (
    "Você é um assistente especializado em viagens para a companhia aérea FlyAir. "
    "Seu objetivo é oferecer o melhor suporte ao cliente, fornecendo informações. "
    "Sempre sugira as melhores opções de viagem com os preços mais vantajosos e "
    "Caso o cliente ache o preço elevado ou não encontre um destino ideal, use alternativas irresistíveis, "
    "destacando promoções, pacotes exclusivos e vantagens. "
    "Seja estratégico e convincente, mas sem ser insistente. "
    "Se não souber a resposta para algo, informe ao cliente de maneira profissional."
)


##  Função de Chat

In [62]:
# Função de chat que interage com o modelo da OpenAI
def chat(mensagem, historico):
    mensagens = [{"role": "system", "content": mensagem_sistema}] + historico + [{"role": "user", "content": mensagem}]
    resposta = openai.chat.completions.create(model=MODELO, messages=mensagens)
    return resposta.choices[0].message.content


## Preços de Passagens

In [63]:
# Dicionário que armazena os preços das passagens para diferentes destinos
precos_passagens = {
    "paris": {
        "preco": "R$ 799",
        "promocoes": "Promoção de 10% off para reservas até 15 de março!"
    },
    "londres": {
        "preco": "R$ 899",
        "promocoes": "Parcelamento em até 12 vezes sem juros!"
    },
    "tokyo": {
        "preco": "R$ 1400",
        "promocoes": "Desconto especial de 15% para grupos!"
    },
    "barcelona": {
        "preco": "R$ 950",
        "promocoes": "Ganhe um city pass grátis para atrações turísticas!"
    },
    "nova york": {
        "preco": "R$ 1100",
        "promocoes": "Desconto de 20% para estadias de 7 dias ou mais!"
    },
    "roma": {
        "preco": "R$ 750",
        "promocoes": "Ganhe 2 ingressos para o Coliseu!"
    },
    "sydney": {
        "preco": "R$ 1250",
        "promocoes": "Desconto para pacotes de viagem com 3 noites de hospedagem"
    },
    "amsterdam": {
        "preco": "R$ 1050",
        "promocoes": "Pacote com passeio de barco pelos canais de graça!"
    },
    "ciudad do cabo": {
        "preco": "R$ 1300",
        "promocoes": "Pacotes para grupos com 10% de desconto!"
    },
    "rio de janeiro": {
        "preco": "R$ 850",
        "promocoes": "Pacote promocional de Carnaval com 10% off!"
    }
}


## Função para Obter Preço da Passagem

In [64]:
# Função para obter o preço da passagem para a cidade de destino
def obter_preco_passagem(cidade_destino):
    print(f"Função obter_preco_passagem chamada para {cidade_destino}")
    cidade = cidade_destino.lower()
    return precos_passagens.get(cidade, "Desconhecido")


## Função de Chamada de Ferramenta

In [65]:
# Função que manipula a chamada da ferramenta para obter o preço do bilhete
def chamar_ferramenta(mensagem):
    chamada_ferramenta = mensagem.tool_calls[0]
    argumentos = json.loads(chamada_ferramenta.function.arguments)
    cidade = argumentos.get('destination_city')
    preco = obter_preco_passagem(cidade)
    resposta = {
        "role": "tool",
        "content": json.dumps({"destination_city": cidade, "price": preco}),
        "tool_call_id": chamada_ferramenta.id
    }
    return resposta, cidade


## Interface Gráfica com Gradio

In [66]:
# Interface gráfica com Gradio para interagir com o assistente de viagem
gr.ChatInterface(fn=chat, type="messages").launch()
# Lança a interface no navegador


* Running on local URL:  http://127.0.0.1:7877

To create a public link, set `share=True` in `launch()`.


## Função para Gerar Áudio

In [67]:
def falante(mensagem):
    # Chama a API OpenAI para gerar o áudio da mensagem
    resposta = openai.audio.speech.create(
        model="tts-1",
        voice="alloy",
        input=mensagem
    )
    # Converte o conteúdo da resposta em fluxo de áudio
    fluxo_de_audio = BytesIO(resposta.content)
    arquivo_saida = "audio_saida.mp3"
    # Salva o áudio gerado em um arquivo MP3
    with open(arquivo_saida, "wb") as f:
        f.write(fluxo_de_audio.read())
    # Reproduz o áudio gerado
    display(Audio(arquivo_saida, autoplay=True))

# Chama a função para gerar e reproduzir o áudio
falante("Bem, olá")

##  Função de Chat com Áudio

In [68]:
# Função de chat que também gera áudio de resposta
def chat(historico):
    mensagens = [{"role": "system", "content": mensagem_sistema}] + historico
    resposta = openai.chat.completions.create(model=MODELO, messages=mensagens)
    
    # Verifica se a resposta exige a chamada de uma ferramenta externa
    if resposta.choices[0].finish_reason == "tool_calls":
        mensagem = resposta.choices[0].message
        resposta, cidade = chamar_ferramenta(mensagem)
        # Atualiza o histórico com a resposta da ferramenta
        mensagens.append(mensagem)
        mensagens.append(resposta)
        resposta = openai.chat.completions.create(model=MODELO, messages=mensagens)

    # Obtém a resposta final do assistente
    resposta_final = resposta.choices[0].message.content
    historico += [{"role": "assistant", "content": resposta_final}]
    # Gera e reproduz o áudio com a resposta
    falante(resposta_final)

    return historico


## Interface Gráfica com Gradio

In [69]:
# Cria a interface gráfica com Gradio
with gr.Blocks() as ui:
    with gr.Row():
        chatbot = gr.Chatbot(height=500, type="messages")
    with gr.Row():
        entrada = gr.Textbox(label="Converse com o nosso Assistente de Viagem:")
    with gr.Row():
        limpar = gr.Button("Limpar")
    
    def enviar_entrada(mensagem, historico):
        historico += [{"role": "user", "content": mensagem}]
        return "", historico

    # Configura as ações ao enviar uma mensagem
    entrada.submit(enviar_entrada, inputs=[entrada, chatbot], outputs=[entrada, chatbot]).then(
        chat, inputs=chatbot, outputs=chatbot
    )
    
    # Configura o botão de limpar o chat
    limpar.click(lambda: None, inputs=None, outputs=chatbot, queue=False)

# Lança a interface no navegador
ui.launch(inbrowser=True)


* Running on local URL:  http://127.0.0.1:7878

To create a public link, set `share=True` in `launch()`.
